In [1]:
import os
import sys
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', 50)

from matplotlib import pyplot as plt
import seaborn as sns
%matplotlib inline

import plotly
import plotly.graph_objs as go
import cufflinks as cf
cf.set_config_file(offline=True)

In [2]:
base_path = os.path.abspath('../..')
data_path = os.path.join(base_path, 'data')
database_path = os.path.join(data_path, 'database')
strategy_path = os.path.join(base_path, 'strategy')
check_path = os.path.join(strategy_path, 'check')
sys.path.append(strategy_path)

In [3]:
from strategy import CommodityStrategy, EquityStrategy, IRStrategy, EmergingStrategy
from tester import Tester

In [4]:
from ICA import ICA
from ICA2 import ICA2
from IEQ import IEQ
from IPM import IPM
from IRV import IRV
from ISS import ISS

In [5]:
# Bond data
JGB_flag = "out"

bond = pd.read_csv(os.path.join(data_path, 'bonds.csv'), header=0, index_col=0, parse_dates=True)
BRet = bond.pct_change(1)
Bindex = (1. + BRet).cumprod().iloc[1:]
Bindex = Bindex / Bindex.iloc[0]
BRet = BRet.iloc[1:]

# 1. ICA

In [6]:
ica = ICA(strategy_name="ICA", asset_type="IR")
# ica.load_index_and_return(from_db=True, save_file=True)
ica.index = Bindex.copy()
ica.ret = BRet.copy()

# ica.load_strategy_data(table='bloom', origin1='bonds2yr', origin2='bonds10yr')
bonds2yr = pd.read_csv(os.path.join(data_path, "bonds2yr.csv"), index_col=0, parse_dates=True)
bonds2yr.index.name = 'tdate'
bonds2yr.columns.name = 'ticker'

bonds10yr = pd.read_csv(os.path.join(data_path, "bonds10yr.csv"), index_col=0, parse_dates=True)
bonds10yr.index.name = 'tdate'
bonds10yr.columns.name = 'ticker'

ica.twoYR = bonds2yr
ica.tenYR = bonds10yr

ica.set_rebalance_period(cs_freq='month', ts_freq='month')
ica.calculate_signal(CS=0.5, nopos=0.4, minobs1=12, use_JGB=False)
ica.set_portfolio_parameter(cs_strategy_type='vol', min_vol=0.04)
ica.make_portfolio()

2020-01-02 10:26:31,879 - ICA - INFO - [STEP 0] START LOGGING ICA
2020-01-02 10:26:31,906 - ICA - INFO - [STEP 2] SET REBALANCE PERIOD
C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\ICA.py:55: FutureWarning:

Currently, 'apply' passes the values as ndarrays to the applied function. In the future, this will change to passing it as Series objects. You need to specify 'raw=True' to keep the current behaviour, and you can pass 'raw=False' to silence this warning

C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\ICA.py:75: FutureWarning:


Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#deprecate-loc-reindex-listlike

C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\ICA.py:76: FutureWarning:


Passing list-likes to .loc or [] wi

In [7]:
start_date = '2001-01-01'
end_date = '2018-05-09'

# get r results
ica_comp_df = pd.read_csv('./past/ica.csv', header=0, index_col=0, parse_dates=True)
ica_lag_comp_df = pd.read_csv('./past/ica_lag.csv', header=0, index_col=0, parse_dates=True)

In [8]:
tester = Tester(ica)
tester.set_period(start=start_date, end=end_date)
tester.run(save_file=False)

2020-01-02 10:26:49,247 - ICA - INFO - [STEP 6] START BACKTEST
2020-01-02 10:26:49,248 - ICA - INFO - [STEP 6 - 1] BACKTEST ICA TIME SERIES
2020-01-02 10:26:49,758 - ICA - INFO - [STEP 6 - 2] BACKTEST ICA CROSS SECTIONAL


In [9]:
to_plot = (1.+ ica_lag_comp_df).loc[start_date:].cumprod()
to_plot['TS_python'] = tester.strategy.TS_result
to_plot['CS_python'] = tester.strategy.CS_result
to_plot.iplot()

# 2. ICA2

In [10]:
ica2 = ICA2(strategy_name="ICA2", asset_type="IR")
# ica2.load_index_and_return(from_db=False, save_file=False)
ica2.index = Bindex.copy()
ica2.ret = BRet.copy()


# ica2.load_strategy_data(table='bloom', origin1='bonds2yr', origin2='bonds10yr')
bonds2yr = pd.read_csv(os.path.join(data_path, "bonds2yr.csv"), index_col=0, parse_dates=True)
bonds2yr.index.name = 'tdate'
bonds2yr.columns.name = 'ticker'

bonds10yr = pd.read_csv(os.path.join(data_path, "bonds10yr.csv"), index_col=0, parse_dates=True)
bonds10yr.index.name = 'tdate'
bonds10yr.columns.name = 'ticker'

ica2.twoYR = bonds2yr.copy()
ica2.tenYR = bonds10yr.copy()

ica2.set_rebalance_period(ts_freq='month', cs_freq='month')
ica2.calculate_signal(CS=0.5, minobs=12, use_JGB=False)
ica2.set_portfolio_parameter(cs_strategy_type='vol', min_vol=0.04)
ica2.make_portfolio()

2020-01-02 10:26:52,629 - ICA2 - INFO - [STEP 0] START LOGGING ICA2
2020-01-02 10:26:52,650 - ICA2 - INFO - [STEP 2] SET REBALANCE PERIOD
C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\ICA2.py:55: FutureWarning:

Currently, 'apply' passes the values as ndarrays to the applied function. In the future, this will change to passing it as Series objects. You need to specify 'raw=True' to keep the current behaviour, and you can pass 'raw=False' to silence this warning

C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\ICA2.py:93: FutureWarning:


Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#deprecate-loc-reindex-listlike

C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\ICA2.py:94: FutureWarning:


Passing list-likes to .loc or

In [11]:
start_date = '2001-01-01'
end_date = '2018-05-09'

# get r results
ica2_comp_df = pd.read_csv('./past/ica2.csv', header=0, index_col=0, parse_dates=True)
ica2_lag_comp_df = pd.read_csv('./past/ica2_lag.csv', header=0, index_col=0, parse_dates=True)

In [12]:
tester = Tester(ica2)
tester.set_period(start=start_date, end=end_date)
tester.run(save_file=False)

2020-01-02 10:27:10,510 - ICA2 - INFO - [STEP 6] START BACKTEST
2020-01-02 10:27:10,510 - ICA2 - INFO - [STEP 6 - 1] BACKTEST ICA2 TIME SERIES
2020-01-02 10:27:11,240 - ICA2 - INFO - [STEP 6 - 2] BACKTEST ICA2 CROSS SECTIONAL


In [13]:
to_plot = (1.+ ica2_lag_comp_df).loc[start_date:].cumprod()
to_plot['TS_python'] = tester.strategy.TS_result
to_plot['CS_python'] = tester.strategy.CS_result
to_plot.iplot()

# 3. IEQ

In [14]:
eindex_path = os.path.join(data_path, 'totindex.csv')
eindex1_path = os.path.join(data_path, 'priceindex.csv')
efuture_path = os.path.join(data_path, 'FutGenratio1.csv')

eindex = pd.read_csv(eindex_path, header=0, index_col=0, parse_dates=True)
eindex1 = pd.read_csv(eindex1_path, header=0, index_col=0, parse_dates=True)
efut = pd.read_csv(efuture_path, header=0, index_col=0, parse_dates=True)

eindex1 = eindex1.loc[:'2008']
ERetp = eindex1.pct_change(1).iloc[1:]
ERett = eindex.pct_change(1).iloc[1:]
fRet = efut.pct_change(1).iloc[1:]

compRet = ERett
compRet[compRet.isna()] = ERetp[compRet.isna()]
ERet1 = compRet
ERet1.drop_duplicates(inplace=True)
fRet.drop_duplicates(inplace=True)
ERet = pd.concat([ERet1.loc[:'2007-12-31'], fRet.loc['2008-01-01':]], axis=0)
ERet.fillna(0)
Eindex = (1 + ERet).cumprod()
Eindex = Eindex / Eindex.iloc[0]

In [15]:
# equity_strategy = EquityStrategy(strategy_name='helper', asset_type='EQUITY')
# equity_strategy.load_index_and_return(from_db=False, save_file=False)
ieq = IEQ(strategy_name="IEQ", asset_type="IR")
ieq.index = Bindex.copy()
ieq.ret = BRet.copy()

# ieq.load_index_and_return(from_db=True, save_file=False)
ieq.Eindex = Eindex.copy()

ieq.set_rebalance_period(ts_freq='month', cs_freq='month')
ieq.calculate_signal(CS=0.5, nopos=0.4, use_JGB=False)
ieq.set_portfolio_parameter(cs_strategy_type='vol', min_vol=0.04)
ieq.make_portfolio()

2020-01-02 10:27:13,779 - IEQ - INFO - [STEP 0] START LOGGING IEQ
2020-01-02 10:27:13,781 - IEQ - INFO - [STEP 2] SET REBALANCE PERIOD
C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\IEQ.py:46: FutureWarning:

Currently, 'apply' passes the values as ndarrays to the applied function. In the future, this will change to passing it as Series objects. You need to specify 'raw=True' to keep the current behaviour, and you can pass 'raw=False' to silence this warning

C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\IEQ.py:72: FutureWarning:


Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#deprecate-loc-reindex-listlike

C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\IEQ.py:73: FutureWarning:


Passing list-likes to .loc or [] wi

In [16]:
start_date = '2001-01-01'
end_date = '2018-05-09'

# get r results
ieq_comp_df = pd.read_csv('./past/ieq.csv', header=0, index_col=0, parse_dates=True)
ieq_lag_comp_df = pd.read_csv('./past/ieq_lag.csv', header=0, index_col=0, parse_dates=True)

In [17]:
tester = Tester(ieq)
tester.set_period(start=start_date, end=end_date)
tester.run(save_file=False)

2020-01-02 10:27:32,159 - IEQ - INFO - [STEP 6] START BACKTEST
2020-01-02 10:27:32,160 - IEQ - INFO - [STEP 6 - 1] BACKTEST IEQ TIME SERIES
2020-01-02 10:27:32,628 - IEQ - INFO - [STEP 6 - 2] BACKTEST IEQ CROSS SECTIONAL


In [18]:
to_plot = (1.+ ieq_lag_comp_df).loc[start_date:].cumprod()
to_plot['TS_python'] = tester.strategy.TS_result
to_plot['CS_python'] = tester.strategy.CS_result
to_plot.iplot()

# 4. IPM

In [19]:
ipm = IPM(strategy_name="IPM", asset_type="IR")
ipm.index = Bindex.copy()
ipm.ret = BRet.copy()

# ipm.load_index_and_return(from_db=False, save_file=False)
ipm.set_rebalance_period(cs_freq='week', ts_freq='week', rebalance_weekday=1)
ipm.calculate_signal(CS=0.5, nopos=0.4, minobs=260, minobs1=52, longlen=52, shortlen=4)
ipm.set_portfolio_parameter(cs_strategy_type='vol', min_vol=0.04)
ipm.make_portfolio()

2020-01-02 10:27:35,496 - IPM - INFO - [STEP 0] START LOGGING IPM
2020-01-02 10:27:35,497 - IPM - INFO - [STEP 2] SET REBALANCE PERIOD
C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\IPM.py:104: FutureWarning:


Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#deprecate-loc-reindex-listlike

C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\IPM.py:105: FutureWarning:


Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#deprecate-loc-reindex-listlike

2020-01-02 10:27:36,113 - IPM - INFO - [STEP 4] SET PORTFOLIO PARAMETER
2020-01-02 10:27:36,114 - IPM - INFO - [STEP 5] MAKE PO

In [20]:
start_date = '2001-01-01'
end_date = '2018-05-09'

# get r results
ipm_comp_df = pd.read_csv('./past/ipm.csv', header=0, index_col=0, parse_dates=True)
ipm_lag_comp_df = pd.read_csv('./past/ipm_lag.csv', header=0, index_col=0, parse_dates=True)

In [21]:
tester = Tester(ipm)
tester.set_period(start=start_date, end=end_date)
tester.run(save_file=False)

2020-01-02 10:27:55,091 - IPM - INFO - [STEP 6] START BACKTEST
2020-01-02 10:27:55,092 - IPM - INFO - [STEP 6 - 1] BACKTEST IPM TIME SERIES
2020-01-02 10:27:55,857 - IPM - INFO - [STEP 6 - 2] BACKTEST IPM CROSS SECTIONAL


In [22]:
to_plot = (1.+ ipm_lag_comp_df).loc[start_date:].cumprod()
to_plot['TS_python'] = tester.strategy.TS_result
to_plot['CS_python'] = tester.strategy.CS_result
to_plot.iplot()

# 5. IRV

In [23]:
irv = IRV(strategy_name="IRV", asset_type="IR")
irv.index = Bindex.copy()
irv.ret = BRet.copy()

# irv.load_index_and_return(from_db=False, save_file=False)
# irv.load_strategy_data1(table='ds', origin='ERR')

err = pd.read_csv(os.path.join(data_path, "ERR.csv"), index_col=0, parse_dates=True)
err.index.name = 'tdate'
err.columns.name = 'ticker'

bonds10yr = pd.read_csv(os.path.join(data_path, "bonds10yr.csv"), index_col=0, parse_dates=True)
bonds10yr.index.name = 'tdate'
bonds10yr.columns.name = 'ticker'

realyield = pd.read_csv(os.path.join(data_path, "realyield.csv"), index_col=0, parse_dates=True)
realyield.index.name = 'tdate'
realyield.columns.name = 'ticker'

realyield2 = pd.read_csv(os.path.join(data_path, "realyield2.csv"), index_col=0, parse_dates=True)
realyield2.index.name = 'tdate'
realyield2.columns.name = 'ticker'

# irv.load_strategy_data2(table='bloom', origin1='bonds10yr', origin2='realyield', origin3='realyield2')
irv.err = err
irv.tenYR = bonds10yr
irv.ry = realyield
irv.ry2 = realyield2

irv.set_rebalance_period(ts_freq='month', cs_freq='month')
irv.calculate_signal(CS=0.5, nopos=0.4, minobs=12, use_JGB=False)
irv.set_portfolio_parameter(cs_strategy_type='vol', min_vol=0.04)
irv.make_portfolio()

2020-01-02 10:27:58,697 - IRV - INFO - [STEP 0] START LOGGING IRV
2020-01-02 10:27:58,715 - IRV - INFO - [STEP 2] SET REBALANCE PERIOD
C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\IRV.py:56: FutureWarning:

Currently, 'apply' passes the values as ndarrays to the applied function. In the future, this will change to passing it as Series objects. You need to specify 'raw=True' to keep the current behaviour, and you can pass 'raw=False' to silence this warning

C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\IRV.py:66: FutureWarning:

Currently, 'apply' passes the values as ndarrays to the applied function. In the future, this will change to passing it as Series objects. You need to specify 'raw=True' to keep the current behaviour, and you can pass 'raw=False' to silence this warning

C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\IRV.py:99: FutureWarning:


Passing list-likes to .loc or [] with any mis

In [24]:
start_date = '2001-01-01'
end_date = '2018-05-09'

# get r results
irv_comp_df = pd.read_csv('./past/irv.csv', header=0, index_col=0, parse_dates=True)
irv_lag_comp_df = pd.read_csv('./past/irv_lag.csv', header=0, index_col=0, parse_dates=True)

In [25]:
tester = Tester(irv)
tester.set_period(start=start_date, end=end_date)
tester.run(save_file=False)

2020-01-02 10:28:15,375 - IRV - INFO - [STEP 6] START BACKTEST
2020-01-02 10:28:15,376 - IRV - INFO - [STEP 6 - 1] BACKTEST IRV TIME SERIES
2020-01-02 10:28:15,892 - IRV - INFO - [STEP 6 - 2] BACKTEST IRV CROSS SECTIONAL


In [26]:
to_plot = (1.+ irv_lag_comp_df).loc[start_date:].cumprod()
to_plot['TS_python'] = tester.strategy.TS_result
to_plot['CS_python'] = tester.strategy.CS_result
to_plot.iplot()

# 6. ISS

In [28]:
iss = ISS(strategy_name="ISS", asset_type="IR")
iss.index = Bindex.copy()
iss.ret = BRet.copy()

# iss.load_index_and_return(from_db=False, save_file=False)
iss.set_rebalance_period(ts_freq='day', cs_freq='month')
iss.calculate_signal(CS=0.5, day1=24, short=0.2, use_JGB=False)
iss.set_portfolio_parameter(cs_strategy_type='vol', min_vol=0.04)
iss.make_portfolio()

2020-01-02 10:40:07,753 - ISS - INFO - [STEP 0] START LOGGING ISS
2020-01-02 10:40:07,753 - ISS - INFO - [STEP 0] START LOGGING ISS
2020-01-02 10:40:07,755 - ISS - INFO - [STEP 2] SET REBALANCE PERIOD
2020-01-02 10:40:07,755 - ISS - INFO - [STEP 2] SET REBALANCE PERIOD
C:\Users\jungyoon.choi\Desktop\jungyoon\project\risk_premia\python\strategy\ISS.py:74: FutureWarning:


Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#deprecate-loc-reindex-listlike

2020-01-02 10:40:08,935 - ISS - INFO - [STEP 4] SET PORTFOLIO PARAMETER
2020-01-02 10:40:08,935 - ISS - INFO - [STEP 4] SET PORTFOLIO PARAMETER
2020-01-02 10:40:08,936 - ISS - INFO - [STEP 5] MAKE PORTFOLIO
2020-01-02 10:40:08,936 - ISS - INFO - [STEP 5] MAKE PORTFOLIO
2020-01-02 10:40:08,937 - ISS - INFO - [STEP 5 - 1] CALCULATE VOLATILITY
2020-01-02 10:40:08

In [29]:
start_date = '2001-01-01'
end_date = '2018-05-09'

# get r results
iss_comp_df = pd.read_csv('./past/iss.csv', header=0, index_col=0, parse_dates=True)
iss_lag_comp_df = pd.read_csv('./past/iss_lag.csv', header=0, index_col=0, parse_dates=True)

In [30]:
tester = Tester(iss)
tester.set_period(start=start_date, end=end_date)
tester.run(save_file=False)

2020-01-02 10:40:21,171 - ISS - INFO - [STEP 6] START BACKTEST
2020-01-02 10:40:21,171 - ISS - INFO - [STEP 6] START BACKTEST
2020-01-02 10:40:21,172 - ISS - INFO - [STEP 6 - 1] BACKTEST ISS TIME SERIES
2020-01-02 10:40:21,172 - ISS - INFO - [STEP 6 - 1] BACKTEST ISS TIME SERIES
2020-01-02 10:40:21,826 - ISS - INFO - [STEP 6 - 2] BACKTEST ISS CROSS SECTIONAL
2020-01-02 10:40:21,826 - ISS - INFO - [STEP 6 - 2] BACKTEST ISS CROSS SECTIONAL


In [31]:
to_plot = (1.+ iss_lag_comp_df).loc[start_date:].cumprod()
to_plot['TS_python'] = tester.strategy.TS_result
to_plot['CS_python'] = tester.strategy.CS_result
to_plot.iplot()